In [2]:
require 'open-uri'
require 'json'
require 'daru'
require 'distribution'
require 'sqlite3' ##This should return true if you have SQLite3 installed


"if(window['d3'] === undefined ||\n   window['Nyaplot'] === undefined){\n    var path = {\"d3\":\"https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.5/d3.min\",\"downloadable\":\"http://cdn.rawgit.com/domitry/d3-downloadable/master/d3-downloadable\"};\n\n\n\n    var shim = {\"d3\":{\"exports\":\"d3\"},\"downloadable\":{\"exports\":\"downloadable\"}};\n\n    require.config({paths: path, shim:shim});\n\n\nrequire(['d3'], function(d3){window['d3']=d3;console.log('finished loading d3');require(['downloadable'], function(downloadable){window['downloadable']=downloadable;console.log('finished loading downloadable');\n\n\tvar script = d3.select(\"head\")\n\t    .append(\"script\")\n\t    .attr(\"src\", \"http://cdn.rawgit.com/domitry/Nyaplotjs/master/release/nyaplot.js\")\n\t    .attr(\"async\", true);\n\n\tscript[0][0].onload = script[0][0].onreadystatechange = function(){\n\n\n\t    var event = document.createEvent(\"HTMLEvents\");\n\t    event.initEvent(\"load_nyaplot\",false,false);\n\t    win

true

In [3]:
Dir[File.join(__dir__, 'library', '*.rb')].each { |file| require file }
# require_relative './library/assignment4'
require './assignment4'
# include Assignment4
require './assignment2'
include Assignment2
require './assignment1'
include Assignment1
require './assignment3'
include Assignment3

Object

## Data Preparation

In [4]:
require 'fileutils'
dir = "#{ENV['HOME']}/cs6140/final_project"
db = SQLite3::Database.open "#{dir}/credit_risk_data.db"
db.results_as_hash = true


true

In [5]:
metadata = db.execute("PRAGMA table_info(application_train);")
column_types = Hash.new
metadata.each do |row|
  column_types[row["name"]] = row["type"]
end
1

1

In [6]:
sql = <<SQL
create temporary view big_table as select 
 app.SK_ID_CURR, app.ext_source_2, app.EXT_SOURCE_1,  AVG_SK_DPD_DEF, MAX_DAYS_CREDIT_ENDDATE, 
  AVG_CNT_DRAWINGS_CURRENT, AVG_DAYS_ENTRY_PAYMENT, AVG_AMT_ANNUITY, app.target
from 
 application_train app 
 left outer join (SELECT SK_ID_CURR, avg(SK_DPD_DEF) as AVG_SK_DPD_DEF 
                  FROM POS_CASH_balance GROUP BY SK_ID_CURR) pos on app.sk_id_curr = pos.sk_id_curr
 left outer join (SELECT SK_ID_CURR, max(DAYS_CREDIT_ENDDATE) as MAX_DAYS_CREDIT_ENDDATE
                  FROM bureau GROUP BY SK_ID_CURR) b on app.sk_id_curr = b.sk_id_curr
 left outer join (SELECT SK_ID_CURR, avg(CNT_DRAWINGS_CURRENT) as AVG_CNT_DRAWINGS_CURRENT 
                  FROM credit_card_balance GROUP BY SK_ID_CURR) cc on app.sk_id_curr = cc.sk_id_curr
 left outer join (SELECT SK_ID_CURR, avg(DAYS_ENTRY_PAYMENT) as AVG_DAYS_ENTRY_PAYMENT 
                  FROM installments_payments GROUP BY SK_ID_CURR) ip on app.sk_id_curr = ip.sk_id_curr
 left outer join (SELECT SK_ID_CURR, avg(AMT_ANNUITY) as AVG_AMT_ANNUITY
                  FROM previous_application GROUP BY SK_ID_CURR) pa on app.sk_id_curr = pa.sk_id_curr
SQL

#drop current table features
begin
db.execute("drop view big_table") 
rescue 
end

db.execute(sql)

[]

In [7]:
# select features and include previous data
data = db.execute("SELECT * FROM big_table limit 10000")
puts data.length
headers =["SK_ID_CURR", "EXT_SOURCE_2", "EXT_SOURCE_1", "AVG_SK_DPD_DEF",  "AVG_AMT_ANNUITY", "TARGET"]
raw = db.execute("select " + headers.join(",") + " from big_table")

1

10000


1

In [8]:
record_counts =db.execute("SELECT count(*) FROM big_table ")
puts record_counts

[{"count(*)"=>307511, 0=>307511}]


In [9]:
#adapt raw data for training
def preprocess meta, headers
  data = []
  
  meta.each do |r|
    row = Hash.new {}
    features = Hash.new {}
    (0..meta[0].length-2).each do |fname|
      features[headers[fname]] = r[fname]
    end    
    row["features"] = features
    row["label"] = r["TARGET"]
    data << row
  end
  
  return data
end

data = preprocess(raw, headers)
puts data[0..1]
1

[{"features"=>{"SK_ID_CURR"=>100002, "EXT_SOURCE_2"=>0.2629485927471776, "EXT_SOURCE_1"=>0.08303696739132256, "AVG_SK_DPD_DEF"=>0.0, "AVG_AMT_ANNUITY"=>9251.775, "TARGET"=>1, nil=>nil}, "label"=>1}, {"features"=>{"SK_ID_CURR"=>100003, "EXT_SOURCE_2"=>0.6222457752555098, "EXT_SOURCE_1"=>0.3112673113812225, "AVG_SK_DPD_DEF"=>0.0, "AVG_AMT_ANNUITY"=>56553.99, "TARGET"=>0, nil=>nil}, "label"=>0}]


1

In [10]:
def filter_nll_column dataset
  corrected_data = []
  dataset.each { |row|
    r  = Hash.new
    features = Hash.new {|h,k| h[k]=0}
    row.each { |j,k|
      if j.class == String
        if j.eql?("TARGET") || j.eql?("target")
          r["label"] = k
        else
          if j.include?("EXT_SOURCE")
            if row[j] == nil or row[j] ==""
              features[j] = 0.0
            else
              features[j] = k.ceil(1)
            end
          else
            features[j]  = k
          end
        end
        r["features"] = features
      end
      }
    corrected_data << r
    }
  return corrected_data
end
1

1

In [11]:
def format_data data
  dataset = []
  data.each { |i|
    temp_hash = Hash.new
    features = Hash.new
    i.each { |j,k|
      if j.class == String
          if j.eql?("TARGET") || j.eql?("target")
            temp_hash["label"] = k
          else
            if k.nil? or k ==""
              k = nil
            else
            features[j] = k
            end
          end
      end
    }
    temp_hash["features"] = features
    dataset << temp_hash
  }
  return dataset
end

:format_data

In [12]:
def encode_categorical data, column_type
  formated = []
  
  feature_values = Hash.new { |h,k| h[k] = []}
  
  data.each do |row|
    temp_hash = Hash.new
    features = Hash.new
    row.each do |k,v|
      if column_type[k].eql?("TEXT")
        if k.eql?("TARGET") || k.eql?("target")
          temp_hash["label"] = v
        end
        
        if !(feature_values[k].index(v).nil?)
          features[k] = feature_values[k].index(v)
        else
          feature_values[k] << v
          features[k] = feature_values[k].index(v)
        end
      elsif column_type[k].eql?("INTEGER")
        if k.eql?("TARGET") || k.eql?("target")
          temp_hash["label"] = v
        end
        if v.nil? or v ==""
#             features[k] = nil
          else
          features[k] = v
          end
      end
    end
    temp_hash["features"] = features
    formated << temp_hash
  end
  return formated
end
1

1

### EXT_SOURCE(orginal)

In [13]:
begin db.execute("drop table cross_validation"); rescue; end
sql = <<SQL
create temp table cross_validation as 
  select sk_id_curr, abs(random()) % 10 as fold
  from application_train
  order by random()
SQL
db.execute(sql)

[]

In [14]:
sql = <<SQL
create temp view example_regression as 
  select a.sk_id_curr, 
  target,
  EXT_SOURCE_1, ext_source_2, ext_source_3,
  fold
  from application_train a inner join cross_validation c on a.sk_id_curr = c.sk_id_curr
SQL
begin db.execute("drop view example_regression"); rescue; end
db.execute(sql)

[]

In [15]:
table = db.execute("select * from example_regression limit 10000")
entries = []
table.each do |r|
  row = Hash.new {|h,k| h[k] = 0.0}
  features = Hash.new {|h,k| h[k] = 0.0}
  ["EXT_SOURCE_1", "EXT_SOURCE_2", "EXT_SOURCE_3"].each.with_index do |k, i|
    features[k] = r[k] == "" ? 0.0 : r[k]
  end
  
  row["features"] = features
  row["label"] = r["TARGET"]
  entries << row
end
puts entries.size
puts entries[0,2]
1

10000
[{"features"=>{"EXT_SOURCE_1"=>0.0, "EXT_SOURCE_2"=>0.26062851599157594, "EXT_SOURCE_3"=>0.6528965519806539}, "label"=>0}, {"features"=>{"EXT_SOURCE_1"=>0.16849340213720335, "EXT_SOURCE_2"=>0.7268614658949519, "EXT_SOURCE_3"=>0.2314393514998941}, "label"=>0}]


1

### Categorical features in application train

In [16]:
cat_app = db.execute("SELECT 
SK_ID_CURR,
TARGET,
CNT_CHILDREN,
FLAG_MOBIL, 
FLAG_EMP_PHONE,
FLAG_WORK_PHONE,
FLAG_CONT_MOBILE,
FLAG_PHONE, 
FLAG_EMAIL,
CNT_FAM_MEMBERS,
REGION_RATING_CLIENT,
REGION_RATING_CLIENT_W_CITY,
HOUR_APPR_PROCESS_START,
REG_REGION_NOT_LIVE_REGION,
REG_REGION_NOT_WORK_REGION,
LIVE_REGION_NOT_WORK_REGION,
REG_CITY_NOT_LIVE_CITY,
REG_CITY_NOT_WORK_CITY,
LIVE_CITY_NOT_WORK_CITY,
NAME_CONTRACT_TYPE,
CODE_GENDER,
FLAG_OWN_CAR,
FLAG_OWN_REALTY,
NAME_TYPE_SUITE,
NAME_INCOME_TYPE,
NAME_EDUCATION_TYPE,
NAME_FAMILY_STATUS, 
NAME_HOUSING_TYPE,
OCCUPATION_TYPE,
WEEKDAY_APPR_PROCESS_START,
ORGANIZATION_TYPE,
EMERGENCYSTATE_MODE,
OBS_30_CNT_SOCIAL_CIRCLE,
DEF_30_CNT_SOCIAL_CIRCLE,
OBS_60_CNT_SOCIAL_CIRCLE,
DEF_60_CNT_SOCIAL_CIRCLE
FROM application_train limit 10000;")
1

1

In [17]:
cat_data = encode_categorical cat_app, column_types
puts cat_data[0..1]
1

[{"label"=>1, "features"=>{"SK_ID_CURR"=>100002, "TARGET"=>1, "CNT_CHILDREN"=>0, "FLAG_MOBIL"=>1, "FLAG_EMP_PHONE"=>1, "FLAG_WORK_PHONE"=>0, "FLAG_CONT_MOBILE"=>1, "FLAG_PHONE"=>1, "FLAG_EMAIL"=>0, "CNT_FAM_MEMBERS"=>1, "REGION_RATING_CLIENT"=>2, "REGION_RATING_CLIENT_W_CITY"=>2, "HOUR_APPR_PROCESS_START"=>10, "REG_REGION_NOT_LIVE_REGION"=>0, "REG_REGION_NOT_WORK_REGION"=>0, "LIVE_REGION_NOT_WORK_REGION"=>0, "REG_CITY_NOT_LIVE_CITY"=>0, "REG_CITY_NOT_WORK_CITY"=>0, "LIVE_CITY_NOT_WORK_CITY"=>0, "NAME_CONTRACT_TYPE"=>0, "CODE_GENDER"=>0, "FLAG_OWN_CAR"=>0, "FLAG_OWN_REALTY"=>0, "NAME_TYPE_SUITE"=>0, "NAME_INCOME_TYPE"=>0, "NAME_EDUCATION_TYPE"=>0, "NAME_FAMILY_STATUS"=>0, "NAME_HOUSING_TYPE"=>0, "OCCUPATION_TYPE"=>0, "WEEKDAY_APPR_PROCESS_START"=>0, "ORGANIZATION_TYPE"=>0, "EMERGENCYSTATE_MODE"=>0, "OBS_30_CNT_SOCIAL_CIRCLE"=>0, "DEF_30_CNT_SOCIAL_CIRCLE"=>0, "OBS_60_CNT_SOCIAL_CIRCLE"=>0, "DEF_60_CNT_SOCIAL_CIRCLE"=>0}}, {"label"=>0, "features"=>{"SK_ID_CURR"=>100003, "TARGET"=>0, "CNT

1

### Finance knowledge data
* CREDIT_INCOME_PERCENT
* ANNUITY_INCOME_PERCENT
* DAYS_EMPLOYED

In [18]:
fin_raw = db.execute("SELECT 
                  TARGET, 
                (AMT_CREDIT/AMT_INCOME_TOTAL) as CREDIT_INCOME_PERCENT,
                (AMT_ANNUITY/AMT_INCOME_TOTAL) as ANNUITY_INCOME_PERCENT, 
                (abs(DAYS_EMPLOYED/DAYS_BIRTH)) as ANNUITY_INCOME_PERCENT
                FROM application_train where AMT_ANNUITY!=0 and AMT_CREDIT!=0 and DAYS_EMPLOYED!=0 order by random() limit 10000; ")
fin_raw.first

{"TARGET"=>0, "CREDIT_INCOME_PERCENT"=>1, "ANNUITY_INCOME_PERCENT"=>0, 0=>0, 1=>1, 2=>0, 3=>0}

In [19]:

fin_know = filter_nll_column fin_raw
# fin_know = format_data fin_know
puts fin_know.first
puts fin_know[0..4]
puts fin_know.size

{"label"=>0, "features"=>{"CREDIT_INCOME_PERCENT"=>1, "ANNUITY_INCOME_PERCENT"=>0}}
[{"label"=>0, "features"=>{"CREDIT_INCOME_PERCENT"=>1, "ANNUITY_INCOME_PERCENT"=>0}}, {"label"=>0, "features"=>{"CREDIT_INCOME_PERCENT"=>1, "ANNUITY_INCOME_PERCENT"=>0}}, {"label"=>1, "features"=>{"CREDIT_INCOME_PERCENT"=>4, "ANNUITY_INCOME_PERCENT"=>0}}, {"label"=>0, "features"=>{"CREDIT_INCOME_PERCENT"=>6, "ANNUITY_INCOME_PERCENT"=>19}}, {"label"=>0, "features"=>{"CREDIT_INCOME_PERCENT"=>3, "ANNUITY_INCOME_PERCENT"=>0}}]
10000


In [20]:
sql_fin = <<SQL
    create temp table domain as
    select TARGET,
    (AMT_CREDIT/AMT_INCOME_TOTAL) as CREDIT_INCOME_PERCENT,
    (AMT_ANNUITY/AMT_INCOME_TOTAL) as ANNUITY_INCOME_PERCENT, 
    (abs(DAYS_EMPLOYED/DAYS_BIRTH)) as ANNUITY_INCOME_PERCENT,
    abs(random()) % 10 as fold
    from application_train where AMT_ANNUITY!=0 and AMT_CREDIT!=0 and DAYS_EMPLOYED!=0 order by random() 
SQL
f_headers=["CREDIT_INCOME_PERCENT","ANNUITY_INCOME_PERCENT","ANNUITY_INCOME_PERCENT"]
1
        

1

In [21]:
# generate train and test dataset each time upon call handles type numeric and categorical in db 
def data_hold_out db,table_name, sql, feature_headers ,type="N",type_column
  data = []
  begin db.execute("drop table #{table_name}"); rescue; end
  db.execute(sql)
  tb = db.execute("select * from "+ table_name + " where fold=abs(random()) % 10 limit 10000")
  if type=="C"
    data = filter_nll_column tb
#     data=encode_categorical tb,type_column
  else
    tb.each do |r|
      row = Hash.new {|h,k| h[k] = 0.0}
      features = Hash.new {|h,k| h[k] = 0.0}
      feature_headers.each.with_index do |k, i|
        features[k] = r[k] == "" ? 0.0 : r[k]
      end
      row["features"] = features
      row["label"] = r["TARGET"]
      data<< row
    end
  end  
  return data
end
1

1

In [22]:
fin_know=data_hold_out db,"domain",sql_fin,f_headers,"C" ,column_types
puts fin_know.first
1

{"label"=>0, "features"=>{"CREDIT_INCOME_PERCENT"=>5, "ANNUITY_INCOME_PERCENT"=>0.3567575757575758, "ANNUITY_INCOME_PERCENT:1"=>0, "fold"=>5}}


1

### Evaluation criteria

 ### sgd prediction score

In [23]:
# prepare the result of hypothesis function for calculating ROC
def score_model(sgd, db)
#   sent = Hash.new
#   header = %w(amt_income_total EXT_SOURCE_1 ext_source_2 ext_source_3).collect {|k| k.upcase}  
  scores = []
  db.execute("select * from example_regression where fold != 0 limit 10000") do |row|
    x = {"features" => Hash.new{|h,k| h[k]=0.0}, "label" => row["TARGET"]}  
    [1,2,3].each do |i|
      if row["EXT_SOURCE_#{i}"].to_f.zero? 
        k = "s_#{i}_nil"
      else
        10.times do |bin|            
          k = "s_#{i}_#{bin}" if row["EXT_SOURCE_#{i}"].to_f >= bin / 10.0
        end
      end
      x["features"][k] = 1.0
    end
#     puts x["features"].class
#     puts x["features"]
#     sent = x
    score = sgd.objective.predict(x, sgd.weights)
    scores << [score, x["label"] > 0.0 ? 1.0 : 0.0]
  end  
#   puts sent
#   puts scores.size
#   puts scores.last
  return scores
end

:score_model

###  fixed& random prediction score

In [24]:
def score_model2 model, data, w
  test =data
  scores = []
  test.each do |row|
    prediction = model.predict(row, w)
    scores << [prediction,row["label"]> 0.0 ? 1.0 : 0.0]
  end
#   puts scores.size
#   puts scores.last
  return scores
end
1

1

In [25]:
def roc_curve(scores)
  total_neg = scores.inject(0.0) {|u,s| u += (1 - s.last)}
  total_pos = scores.inject(0.0) {|u,s| u += s.last}
  c_neg = 0.0
  c_pos = 0.0
  fp = [0.0]
  tp = [0.0]
  auc = 0.0
  scores.sort_by {|s|
#     puts s 
    -s.first}.each do |s|
    c_neg += 1 if s.last <= 0
    c_pos += 1 if s.last > 0  

    fpr = c_neg / total_neg
    tpr = c_pos / total_pos
    auc += 0.5 * (tpr + tp.last) * (fpr - fp.last)
    fp << fpr
    tp << tpr
  end
  return [fp, tp, auc]
end

:roc_curve

### 1. Logistic Regression

under I.I.D Likelyhood:

* Likeklyhood $P(D \mid z) = \prod_{i = 1}^{n} h(y=1 \mid z)^{y_{i}}  h(y=0 \mid z)^{1 - y_{i}} = \prod_{i = 1}^{n} \frac{1}{1+e^{-z}}^{y_{i}} (\frac{e^{-z}}{1+e^{-z}})^{(1-y_{i})} $

* Use negative log form to construct objective function:

$l_{w}(X,Y) = -\ln P(D \mid z) $

$= -\sum_{i} {y_{i}\ln\frac{1}{1+e^{-z}} + (1-y_{i})\ln\frac{e^{-z}}{1+e^{-z}}} $

$= \sum_{i} \ln (1+e^{-z}) + z (1-y_{i}) $

In [26]:
class LogisticRegressionModel
  
  def func dataset, w
    dataset.inject(0.0) do |u,row| 
      y = row["label"].to_f > 0 ? 1.0 : -1.0
      y_hat = dot(row,w)
      u += Math.log(1 + Math.exp(-y * y_hat))
    end
  end
  
  def grad dataset, w
    g = Hash.new {|h,k| h[k] = 0.0}
    dataset.each {|row| 
      x = row["features"]
      y = row["label"].to_f > 0 ? 1.0 : 0.0
      y_hat = dot(row,w)
      syh = sigmoid(y_hat)
      x.each_key {|k|
        g[k] += (syh - y) * x[k]
        }
      }
    g.each_key {|k| g[k] /= dataset.size}
    return g
  end
  
  def sigmoid x
    return 1.0 / (1 + Math.exp(-x))
  end
  
  # prediction for data entry is the sigmoid function of its inner product 
  def predict row, w   
    y_hat = dot(row,w)
    score=sigmoid(y_hat) #<0.5? 0 : 1
    
    return score
  end
  
  ## Adjusts the parameter to be within the allowable range
  def adjust w
  end
end
1

1

In [27]:
#Stochastic method
# using stochastic gradient descent to train data from db table.
def train_model db, sgd, w, n_max = -1
  i = 1
  iters = []
  lik = []
  entries=[]

#   header = %w(EXT_SOURCE_1 ext_source_2 ext_source_3).collect {|k| k.upcase}
  if n_max == -1
    n = db.execute("select count(*) as n from example_regression where fold != 0").first["n"]
  else
    n = n_max
  end
  #size of one pass
  batch_size = 500
  t_lik = 0.0

  0.step(n, batch_size) do |offset|
    rows = db.execute("select * from example_regression where fold != 0 limit #{batch_size} offset #{offset}")
    batch = rows.collect do |row|
      x = {"features" => Hash.new, "label" => row["TARGET"]}  
      ["EXT_SOURCE_1", "EXT_SOURCE_2", "EXT_SOURCE_3"].each do |i|
        if row[i].to_f.zero? 
#           puts "nil"
          k = "s_#{i}_nil"
        else
          10.times do |bin|            
            k = "s_#{i}_#{bin}" if row[i].to_f >= bin / 10.0
          end
        end
        x["features"][k] = 1.0
        entries << x
      end
      x
    end
    sgd.update batch
    iters << i
    t_lik += sgd.objective.func(batch, sgd.weights)
    lik << t_lik / i
    puts [i, lik.last].join("\t") if i % 10000 == 1 
    i += batch.size
  end
  puts iters.size,lik.size
  puts sgd.weights
  return [iters, lik,sgd.weights]
end

:train_model

In [28]:
class StochasticGradientDescent
  attr_reader :weights
  attr_reader :objective
  #initalize the objective function, weights, iteration count and learning rate
  def initialize obj, w_0, lr = 0.01
    @objective = obj
    @weights = w_0
    @n = 1.0
    @eta = lr
  end
  
  def update data
    eta1=@eta
    gradient=@objective.grad(data,weights)
    lr = eta1/Math.sqrt(@n)
    gradient.each_key{|i|
      @weights[i]-= lr*gradient[i] 
      }
    @objective.adjust(@weights)
    @n+= 1
  end
  
  def train_sgd data,batch_size,iter_max
#     weights=@weights
    i=0
    iters=[]
    lik=[]
    norms=[]
    sum_rmse=[]
    rmses=0.0
    iter_max.times do
      data.shuffle.each_slice(batch_size) do |batch|
        self.update batch
        rmse = @objective.func(batch,@weights)
        iters << i
        lik << rmse
        rmses += rmse
        i += batch.size
        sum_rmse << rmses/i
        norms << norm(@weights)
      end
    end
    return iters,lik,sum_rmse,@weights
  end

end

:train_sgd

In [29]:
w = Hash.new {|h,k| h[k] = rand - 0.5}
sgd_lr = StochasticGradientDescent.new LogisticRegressionModel.new, w, 0.1
iters, lik = train_model db,sgd_lr, w, 50000
iters.shift
lik.shift
1
plot(iters, lik)

1	330.4271048215745
10001	0.6614933384085034
20001	0.6230010552439883
30001	0.6018278686873916
40001	0.5875075279449532
50001	0.5751366631608062
101
101
{"s_EXT_SOURCE_1_nil"=>-0.15362767385835116, "s_EXT_SOURCE_2_2"=>0.16467600303929086, "s_EXT_SOURCE_3_6"=>-0.2488939722419423, "s_EXT_SOURCE_1_1"=>-0.34048709138515243, "s_EXT_SOURCE_2_7"=>-0.5052729024971055, "s_EXT_SOURCE_3_2"=>-0.40391763052951263, "s_EXT_SOURCE_2_4"=>-0.2170681988959311, "s_EXT_SOURCE_3_nil"=>0.2051964697979923, "s_EXT_SOURCE_2_5"=>-0.45048487753615357, "s_EXT_SOURCE_3_4"=>-0.5423720162081012, "s_EXT_SOURCE_1_5"=>-0.31789577635620786, "s_EXT_SOURCE_2_6"=>-0.0062398360631138825, "s_EXT_SOURCE_1_6"=>0.01638687802948922, "s_EXT_SOURCE_2_3"=>-0.28966795499104914, "s_EXT_SOURCE_1_7"=>-0.5214661611663626, "s_EXT_SOURCE_3_7"=>-0.04060768292695602, "s_EXT_SOURCE_1_4"=>-0.3056799884654564, "s_EXT_SOURCE_3_5"=>-0.09134029078026916, "s_EXT_SOURCE_1_2"=>-0.011906896057874773, "s_EXT_SOURCE_3_3"=>-0.3349966646132736, "s_EXT_SOU

#<Nyaplot::Plot:0x007fd6be8e0570 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6bd891980 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"cd51769b-c0b5-463d-992a-9af2a5c2e8cf"}, @xrange=[501, 50001], @yrange=[0.5751366631608062, 1.3170889624464426]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[501, 50001], :yrange=>[0.5751366631608062, 1.3170889624464426]}}>

In [30]:
fp, tp, auc = roc_curve(score_model(sgd_lr, db))
puts auc
plot(fp, tp)

0.5365991159477795


#<Nyaplot::Plot:0x007fd6e9491de0 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6d84aa1d0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"6aeda27b-a924-4a1f-ad4b-a1e4ba1d96ba"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[0.0, 1.0], :yrange=>[0.0, 1.0]}}>

#### 2.Naive Bayes
* Model bias

**Likelyhood function: $p(c_{k} \mid x_{i}) \propto p(c_{k}) \prod_{j} p_{j,k} ^ {x_{i,j}}$**

where $c_{k}$ is the class, $p_{j,k}$ is the probability per class and feature, and $x_{i}$ is the value of the $j$th feature within the $i$th example, $x_{i}$. 

**Objective function: $\quad NLL = -\ln p(c_{k}) \prod_{j} p_{j,k} ^ {x_{i,j}} = -\ln p(c_{k}) - \sum_{j} x_{i,j} \ln p_{j,k} $**

* Single pass implementation:  $\frac{\partial}{\partial p_{j,k}}NLL = \frac{\partial}{\partial p_{j,k}}\{-\ln p(c_{k}) - \sum_{j} x_{i,j} \ln p_{j,k}\} = 0  \implies -\frac{x_{i, j}}{p{j, k}} = 0$


In [31]:
class NaiveBayesOne
  # In one pass nb we pass data entry label and increment the weight by count
  @cls= Hash.new{|h,k| h[k] = 0.0}

  def train_naive_bayes dataset
    weight = Hash.new {|h,k| h[k] = 0.0}
    #one pass for class prior
    dataset.each do |i|
      @cls["#{i["label"]}"] += 1.0
    end
    #one pass for conditional probablity
    dataset.each do |i|
      f = i["features"]
      weight["#{i["label"]}"] += 1.0/dataset.length

      f.each do |j,k|
        weight["#{i["label"]}_#{j}"] += 1.00/@cls["#{i["label"]}"]
      end
    end
    return weight
  end


  def predict_naive_bayes weigh, row

    best_score = 0.0
    best_lbl = ""

    score = Hash.new {|h,k| h[k]=0.0}
    @cls.keys.each do |i|
      score[i] += Math.log(weigh[i])
      row["features"].each do |j,k|
        score[i] += k*Math.log(weigh["#{i}_#{j}"])
      end
    end
    best_score = score.values.max
    best_lbl = score.key(best_score)
    return best_score
  end
end
1

1

#### Naive Bayes Multinomial

In [32]:
class NaiveBayesModel
  # Negative log likelihood
  def func dataset, w
    # class priro follows multinomial
    u = 0.0
    dataset.each {|r|
      s = r["features"]
      k = r["label"]
      u -= Math.log(w[k])
      s.keys.each {|j|
        p_jk = j.to_s + "_" + k.to_s
        u -= s[j] * Math.log(w[p_jk])
        }
      }
    return u
  end
  
  def grad dataset, w
    g = Hash.new {|h,k| h[k] = 0.0}
    
    dataset.each do |r|
      s = r["features"]
      k = r["label"]
      g[k] -= 1 / w[k]
      s.keys.each do |j|
        p_jk = j.to_s + "_" + k.to_s
        g[p_jk] -= s[j] / w[p_jk]
      end
    end
    
    return g
  end
  
  def predict row, w
    s = Hash.new {|h,k| h[k] = 0.0}

    ["0", "1"].each {|k|
      s[k] += Math.log(w[k])
      row["features"].keys.each {|j|
        p_jk = j.to_s + "_" + k.to_s
        s[k] += row["features"][j] * Math.log(w[p_jk])
        }
      }
    score= s.values.max
    return score
  end
  
  def adjust w
    w.each_key do |fname|
      w[fname] = [[0.001, w[fname]].max, 0.999].min
    end
  end
end

:adjust

In [33]:
w = Hash.new {|h,k| h[k] = 0.5}
sgd_nb = StochasticGradientDescent.new NaiveBayesModel.new, w, 1e-3
iters, lik,lik_t,wnb = sgd_nb.train_sgd cat_data,1000,20
iters.shift
lik_t.shift
1
plot(iters, lik_t)

#<Nyaplot::Plot:0x007fd6d7dd1a70 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6d7ca36a8 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"7b439d24-5596-400d-9b7f-0a3730d10488"}, @xrange=[1000, 199000], @yrange=[105.97779782852166, 106.59261085305735]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[1000, 199000], :yrange=>[105.97779782852166, 106.59261085305735]}}>

In [34]:
fp, tp, auc = roc_curve(score_model2(NaiveBayesModel.new,cat_data,wnb))
puts auc
plot(fp, tp)

0.48903701372497554


#<Nyaplot::Plot:0x007fd6d7ae9808 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6d391a148 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"ff3629a7-df2b-4bed-abdb-b71666afb173"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[0.0, 1.0], :yrange=>[0.0, 1.0]}}>

### 3.FixedClassifier
* This classifier always predict 1.

In [35]:
class FixedClassifier
  #only functional part of this model
  def predict data, w
    return 1
  end
end

:predict

In [36]:
w = Hash.new{|h,k| h[k]=0.0}
fc=FixedClassifier.new
scores=score_model2 fc,fin_know,w
fp, tp, auc = roc_curve(scores)
puts auc
plot(fp, tp)


0.5081034723683543


#<Nyaplot::Plot:0x007fd6d07d0b28 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6bc1530c0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"f33bd0c6-e723-48a3-86b4-452e9ec3fbea"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[0.0, 1.0], :yrange=>[0.0, 1.0]}}>

### 4. Random  classifier 

$(Predict= rand < P_{target = 1})$

In [37]:
class RandClassifier
  def train dataset
    size = dataset.length
    probablity = Hash.new{|h,k| h[k]=0.0}
    
    dataset.each do |row|
      probablity[row["label"]] += 1.0/size
    end
    temp_variable = 0.0
    return w = probablity
  end
  
  def predict data,w
    random_number = rand
    w.each { |key, value|
      if random_number > value
        return 1
      end
      }
    return 0
  end

end

:predict

In [38]:
# insert into train and test dataset
def split_data x, index
  test = []
  train = []
  
  x.each_with_index do |i,j|
    if j==(index)
      test = i
    else
      train << i
    end
  end
  train = train.flatten
  
  return [train,test]
end


:split_data

In [39]:
w = Hash.new{|h,k| h[k]=0.0}
randclf=RandClassifier.new
wrand=randclf.train fin_know
# puts wrand.class
# puts acc
scores=score_model2 randclf,fin_know,wrand
puts scores.first
fp, tp, auc = roc_curve(scores)
puts auc
plot(fp, tp)

[1, 0.0]
0.5044526500496223


#<Nyaplot::Plot:0x007fd6bba1a1a0 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6d6d696d8 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"ba097465-c42c-464e-b202-8d497501a04b"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[0.0, 1.0], :yrange=>[0.0, 1.0]}}>

In [40]:
# acc= k_fold_test 10,fin_know,randclf

In [41]:
def confusion_matrix cls_names, x, predictions
      counts = Hash.new {|h,k| h[k] = Hash.new {|h,k| h[k] = 0}}
      cls_names.each {|i| cls_names.each{|j| counts[i][j] = 0}}

      x.each.with_index do |row, i|
        predicted_label = predictions[i].keys.first
        actual_label = row["label"]

        counts[predicted_label][actual_label] += 1
      end

      return counts
end

:confusion_matrix

### Feature Engineering

#### polynomial

In [42]:
sql_p = <<SQL
    create temp table polynomial as 
    select target, EXT_SOURCE_1 * EXT_SOURCE_1 as EXT_1P2,
    EXT_SOURCE_2*EXT_SOURCE_2 as EXT_2P2,
    EXT_SOURCE_3*EXT_SOURCE_3 as EXT_3P2,
    EXT_SOURCE_1,
    EXT_SOURCE_2,
    EXT_SOURCE_3,
    EXT_SOURCE_1*EXT_SOURCE_2 as EXT_12,
    EXT_SOURCE_1*EXT_SOURCE_3 as  EXT_13,
    EXT_SOURCE_3*EXT_SOURCE_2 as EXT_23,
    (EXT_SOURCE_1*EXT_SOURCE_2*EXT_SOURCE_3) EXT_123,
    abs(random()) % 10 as fold
    from application_train where EXT_SOURCE_1!="" and EXT_SOURCE_2!="" and EXT_SOURCE_3!="" order by random() 
SQL
1

1

### Before and after feature engineering

### Logistic Regression

In [57]:
w = Hash.new {|h,k| h[k] = 0.1}
logis =LogisticRegressionModel.new
sgd_lr = StochasticGradientDescent.new LogisticRegressionModel.new, w, 0.1
iters, t_lik,wlr0 = train_model db,sgd_lr, w, 50000
iters.shift
t_lik.shift

1	406.8154296586217
10001	0.7959858607321906
20001	0.7478006306612445
30001	0.7208065890508952
40001	0.7015966202650471
50001	0.686127508831626
101
101
{"s_EXT_SOURCE_1_nil"=>-0.3237677053717553, "s_EXT_SOURCE_2_2"=>0.04338661299651882, "s_EXT_SOURCE_3_6"=>-0.031852680416245685, "s_EXT_SOURCE_1_1"=>0.078482406425644, "s_EXT_SOURCE_2_7"=>-0.03364483893938507, "s_EXT_SOURCE_3_2"=>0.04998233904865521, "s_EXT_SOURCE_2_4"=>0.0015582198710834012, "s_EXT_SOURCE_3_nil"=>-0.05381367378858038, "s_EXT_SOURCE_2_5"=>-0.059752080295198115, "s_EXT_SOURCE_3_4"=>0.0036297669128048924, "s_EXT_SOURCE_1_5"=>0.041935130842702784, "s_EXT_SOURCE_2_6"=>-0.12200983660027608, "s_EXT_SOURCE_1_6"=>0.04349125796376013, "s_EXT_SOURCE_2_3"=>0.030050615969659925, "s_EXT_SOURCE_1_7"=>0.044405771367316264, "s_EXT_SOURCE_3_7"=>-0.0059580517122839825, "s_EXT_SOURCE_1_4"=>0.04265846734386418, "s_EXT_SOURCE_3_5"=>-0.021290840601102392, "s_EXT_SOURCE_1_2"=>0.06014227625835018, "s_EXT_SOURCE_3_3"=>0.02284435888524617, "s_EXT

406.8154296586217

In [44]:
plot(iters, t_lik)

#<Nyaplot::Plot:0x007fd6cfb11860 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6e93e95c8 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"c2cae019-ce7d-4d45-8bfb-d0fa06c95752"}, @xrange=[501, 50001], @yrange=[0.686127508831626, 1.6187017712591316]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[501, 50001], :yrange=>[0.686127508831626, 1.6187017712591316]}}>

In [45]:
fp1, tp1, auc = roc_curve(score_model(sgd_lr,db))
puts auc
plot(fp1, tp1)


0.5003321479740188


#<Nyaplot::Plot:0x007fd6d71d2e40 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6d447adf8 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"b5a5c127-a50c-4886-b5a2-abb9ccecb16c"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[0.0, 1.0], :yrange=>[0.0, 1.0]}}>

In [46]:
feature_headers =["EXT_SOURCE_1", "EXT_SOURCE_2", "EXT_SOURCE_3","EXT_1P2","EXT_2P2","EXT_3P2","EXT_12","EXT_13","EXT_23","EXT_123"]
data_ext1 = data_hold_out db, "polynomial", sql_p, feature_headers,column_types
w = Hash.new {|h,k| h[k] = 0.1}
logis=LogisticRegressionModel.new
sgd_lr = StochasticGradientDescent.new logis, w, 0.1
iters, lik,lik_t,wlr = sgd_lr.train_sgd data_ext1,500,20
1

1

In [47]:
data_ext1 = data_hold_out db, "polynomial", sql_p, feature_headers,column_types
fp3, tp3, auc = roc_curve(score_model2(logis, data_ext1,wlr))
puts auc
plot(fp3, tp3)

0.7356500250382056


#<Nyaplot::Plot:0x007fd6bdb085d8 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6d772bae0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"6dac8b47-98f6-4991-bd70-d1e973ea528c"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[0.0, 1.0], :yrange=>[0.0, 1.0]}}>

### Naive Bayes

In [48]:
w = Hash.new {|h,k| h[k] = 0.5}
sgd_nb = StochasticGradientDescent.new NaiveBayesModel.new, w, 1e-3
iters, lik,lik_t,wnb2 = sgd_nb.train_sgd data_ext1,1000,20
iters.shift
lik.shift
1
plot(iters, lik)

#<Nyaplot::Plot:0x007fd6bbc79338 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6bd20c6f0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"1afdfa01-715a-4905-9f0e-4487f9aed187"}, @xrange=[1000, 199000], @yrange=[6.824565724455316, 152.09518856783808]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[1000, 199000], :yrange=>[6.824565724455316, 152.09518856783808]}}>

In [49]:
fp, tp, auc = roc_curve(score_model2(NaiveBayesModel.new,data_ext1,wnb2))
puts auc
plot(fp, tp)

0.7363278946826871


#<Nyaplot::Plot:0x007fd6d7dc87b8 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6d36a0bd8 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"1a7b87af-df16-4316-a451-283f33ccb3b4"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[0.0, 1.0], :yrange=>[0.0, 1.0]}}>

### Finance related knowledge

In [55]:
# Logistic Regression on new feature space
fin_know=data_hold_out db,"domain",sql_fin,f_headers,"C" ,column_types
w = Hash.new {|h,k| h[k] = 0.1}
logis=LogisticRegressionModel.new
sgd_lr = StochasticGradientDescent.new logis, w, 0.1
iters, lik,lik_t,wlrf = sgd_lr.train_sgd fin_know,100,20
fp2, tp2, auc = roc_curve(score_model2(logis, fin_know,wlrf))
puts auc
plot(fp2, tp2)

0.5219007603624976


#<Nyaplot::Plot:0x007fd6d6dfb9e8 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6d0752bd8 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"29799866-92ec-43c0-9ccb-03dc4be42379"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[0.0, 1.0], :yrange=>[0.0, 1.0]}}>

In [56]:
#NaiveBayes on new feature space
w = Hash.new {|h,k| h[k] = 0.5}
sgd_nb = StochasticGradientDescent.new NaiveBayesModel.new, w, 1e-3
iters, lik,lik_t,wnb3 = sgd_nb.train_sgd data_ext1,1000,20
fp, tp, auc = roc_curve(score_model2(logis, fin_know,wnb3))
puts auc
plot(fp, tp)

0.46887334622077076


#<Nyaplot::Plot:0x007fd6d73515c8 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6d2d10758 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y}, :data=>"6c38dfe2-02cd-4dcf-8889-0fc563d89e60"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>], :options=>{:x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>700, :xrange=>[0.0, 1.0], :yrange=>[0.0, 1.0]}}>

In [52]:
Daru.plotting_library = :gruff

:gruff

In [53]:
df = Daru::DataFrame.new({
   tpr1: tp1, fpr1: fp1,
   tpr2: tp2, fpr2: fp2,
   tpr3: tp3, fpr3: fp3})
df
1
df.head
1

1

In [54]:
df.plot type: :line, x: [:fpr1, :fpr2, :fpr3], y: [:tpr1, :tpr2, :tpr3]

#<Nyaplot::Plot:0x007fd6d471b670 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fd6d85b9558 @properties={:type=>:line, :options=>{:x=>:fpr1, :y=>:tpr1}, :data=>"9f8977f4-52bf-4b0c-9edc-4ba0a8ad4aeb"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>, #<Nyaplot::Diagram:0x007fd6d85b9030 @properties={:type=>:line, :options=>{:x=>:fpr2, :y=>:tpr2}, :data=>"9f8977f4-52bf-4b0c-9edc-4ba0a8ad4aeb"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>, #<Nyaplot::Diagram:0x007fd6d85b8ae0 @properties={:type=>:line, :options=>{:x=>:fpr3, :y=>:tpr3}, :data=>"9f8977f4-52bf-4b0c-9edc-4ba0a8ad4aeb"}, @xrange=[0.0, 1.0], @yrange=[0.0, 1.0]>], :options=>{:zoom=>true, :width=>700, :xrange=>[0.0, 1.0], :yrange=>[0.0, 1.0]}}>